### Content Based Recommendations

In the previous notebook, you were introduced to a way of making recommendations using collaborative filtering.  However, using this technique there are a large number of users who were left without any recommendations at all.  Other users were left with fewer than the ten recommendations that were set up by our function to retrieve....

In order to help these users out, let's try another technique: **content based** recommendations. Let's start off where we were in the previous notebook.

In [1]:
import pandas as pd
import numpy as np
import pickle

In [2]:
# Read the datasets
movies = pd.read_csv('movies_clean.csv', index_col='movie_id')
del movies['Unnamed: 0']

reviews = pd.read_csv('reviews_clean.csv', index_col=0)
all_recs = pickle.load(open("all_recs.p", "rb"))

In [4]:
movies.head()

movie  \
movie_id                                                      
8             Edison Kinetoscopic Record of a Sneeze (1894)   
10                      La sortie des usines Lumière (1895)   
12                            The Arrival of a Train (1896)   
25        The Oxford and Cambridge University Boat Race ...   
91                               Le manoir du diable (1896)   

                      genre  date  1800's  1900's  2000's  History  News  \
movie_id                                                                   
8         Documentary|Short  1894       1       0       0        0     0   
10        Documentary|Short  1895       1       0       0        0     0   
12        Documentary|Short  1896       1       0       0        0     0   
25                      NaN  1895       1       0       0        0     0   
91             Short|Horror  1896       1       0       0        0     0   

          Horror  Musical  ...  Fantasy  Romance  Game-Show  Action  \
movie_id                   ...                                        
8              0        0  ...        0        0          0       0   
10             0        0  ...        0        0          0       0   
12             0        0  ...        0        0          0       0   
25             0        0  ...        0        0          0       0   
91             1        0  ...        0        0          0       0   

          Documentary  Animation  Comedy  Short  Western  Thriller  
movie_id                                                            
8                   1          0       0      1        0         0  
10                  1          0       0      1        0         0  
12                  1          0       0      1        0         0  
25                  0          0       0      0        0         0  
91                  0          0       0      1        0         0  

[5 rows x 34 columns]

In [5]:
reviews.head()

user_id  movie_id  rating   timestamp                 date  month_1  \
0        1     68646      10  1381620027  2013-10-12 23:20:27        0   
1        1    113277      10  1379466669  2013-09-18 01:11:09        0   
2        2    422720       8  1412178746  2014-10-01 15:52:26        0   
3        2    454876       8  1394818630  2014-03-14 17:37:10        0   
4        2    790636       7  1389963947  2014-01-17 13:05:47        0   

   month_2  month_3  month_4  month_5  ...  month_9  month_10  month_11  \
0        0        0        0        0  ...        0         1         0   
1        0        0        0        0  ...        0         0         0   
2        0        0        0        0  ...        0         1         0   
3        0        0        0        0  ...        0         0         0   
4        0        0        0        0  ...        0         0         0   

   month_12  year_2013  year_2014  year_2015  year_2016  year_2017  year_2018  
0         0          1          0          0          0          0          0  
1         0          1          0          0          0          0          0  
2         0          0          1          0          0          0          0  
3         0          0          1          0          0          0          0  
4         0          0          1          0          0          0          0  

[5 rows x 23 columns]

In [6]:
all_recs

{2: ['Philadelphia (1993)',
  'Training Day (2001)',
  'About Schmidt (2002)',
  'Insomnia (2002)',
  'The United States of Leland (2003)',
  'Shattered Glass (2003)',
  'Man on Fire (2004)',
  'Flipped (2010)',
  'Silver Linings Playbook (2012)',
  'Lawless (2012)',
  '50/50 (2011)',
  'Crazy, Stupid, Love. (2011)',
  'The Perks of Being a Wallflower (2012)',
  'Before I Go to Sleep (2014)',
  'Zero Dark Thirty (2012)',
  'American Hustle (2013)',
  'Django Unchained (2012)',
  'Side Effects (2013)',
  'Gone Girl (2014)',
  'Enough Said (2013)',
  'Nightcrawler (2014)'],
 3: ['Basic Instinct (1992)',
  'The Shawshank Redemption (1994)',
  'The Wedding Ringer (2015)',
  'Life as We Know It (2010)',
  'The Hangover (2009)',
  'Limitless (2011)',
  'The Great Gatsby (2013)',
  'This Is Where I Leave You (2014)',
  'Inception (2010)',
  "The King's Speech (2010)",
  'Love, Rosie (2014)',
  'Now You See Me (2013)',
  'The Intouchables (2011)',
  'Safe Haven (2013)',
  'Before I Go to Sleep

### Datasets

From the above, you now have access to three important items that you will be using throughout the rest of this notebook.  

`a.` **movies** - a dataframe of all of the movies in the dataset along with other content related information about the movies (genre and date)


`b.` **reviews** - this was the main dataframe used before for collaborative filtering, as it contains all of the interactions between users and movies.


`c.` **all_recs** - a dictionary where each key is a user, and the value is a list of movie recommendations based on collaborative filtering

For the individuals in **all_recs** who did receive 10 recommendations using collaborative filtering, we don't really need to worry about them.  However, there were a number of individuals in our dataset who did not receive any recommendations.

-----

`1.` Let's start with finding all of the users in our dataset who didn't get all 10 ratings we would have liked them to have using collaborative filtering.  

In [9]:
users_with_all_recs = set([k for k in all_recs if len(all_recs[k]) >= 10]) # Store user ids who have all their recommendations in this (10 or more)
all_users = reviews['user_id'].unique().tolist()
users_who_need_recs = [uid for uid in all_users if uid not in users_with_all_recs]# Store users who still need recommendations here
# all_users

In [10]:
print(len(users_with_all_recs))
print(len(users_who_need_recs))

22187
31781


In [11]:
# A quick test
assert len(users_with_all_recs) == 22187
print("That's right there were still another 31781 users who needed recommendations when we only used collaborative filtering!")

That's right there were still another 31781 users who needed recommendations when we only used collaborative filtering!


### Content Based Recommendations

You will be doing a bit of a mix of content and collaborative filtering to make recommendations for the users this time.  This will allow you to obtain recommendations in many cases where we didn't make recommendations earlier.     

`2.` Before finding recommendations, rank the user's ratings from highest to lowest. You will move through the movies in this order looking for other similar movies.

In [83]:
# create a dataframe similar to reviews, but ranked by rating for each user
ranked_ratings = reviews.sort_values(by=['user_id', 'rating'], ascending=[True, False])
ranked_ratings

user_id  movie_id  rating   timestamp                 date  month_1  \
0             1     68646      10  1381620027  2013-10-12 23:20:27        0   
1             1    113277      10  1379466669  2013-09-18 01:11:09        0   
16            2   1798709      10  1389948338  2014-01-17 08:45:38        0   
18            2   2024544      10  1389355949  2014-01-10 12:12:29        0   
22            2   2726560       9  1438293988  2015-07-30 22:06:28        0   
...         ...       ...     ...         ...                  ...      ...   
712305    53966   5462326       1  1517615143  2018-02-02 23:45:43        0   
712328    53966   6265828       1  1505940901  2017-09-20 20:55:01        0   
712334    53967    816711       8  1371972851  2013-06-23 07:34:11        0   
712335    53968   1559547       2  1373287369  2013-07-08 12:42:49        0   
712336    53968   2415464       2  1373772560  2013-07-14 03:29:20        0   

        month_2  month_3  month_4  month_5  ...  month_9  month_10  month_11  \
0             0        0        0        0  ...        0         1         0   
1             0        0        0        0  ...        0         0         0   
16            0        0        0        0  ...        0         0         0   
18            0        0        0        0  ...        0         0         0   
22            0        0        0        0  ...        0         0         0   
...         ...      ...      ...      ...  ...      ...       ...       ...   
712305        0        0        0        0  ...        0         0         0   
712328        0        0        0        0  ...        0         0         0   
712334        0        0        0        0  ...        0         0         0   
712335        0        0        0        0  ...        0         0         0   
712336        0        0        0        0  ...        0         0         0   

        month_12  year_2013  year_2014  year_2015  year_2016  year_2017  \
0              0          1          0          0          0          0   
1              0          1          0          0          0          0   
16             0          0          1          0          0          0   
18             0          0          1          0          0          0   
22             0          0          0          1          0          0   
...          ...        ...        ...        ...        ...        ...   
712305         0          0          0          0          0          0   
712328         0          0          0          0          0          1   
712334         0          1          0          0          0          0   
712335         0          1          0          0          0          0   
712336         0          1          0          0          0          0   

        year_2018  
0               0  
1               0  
16              0  
18              0  
22              0  
...           ...  
712305          1  
712328          0  
712334          0  
712335          0  
712336          0  

[712337 rows x 23 columns]

### Similarities

We have talked in our first Lecture at ITI about similarity metrics and the difference between dot product vs. cosine similarity vs euclidean distance. Here we will apply what we have learnt. 


In many cases, it turns out that one of the fastest ways we can find out how similar items are to one another (when our matrix isn't totally sparse like it was in the earlier section) is by simply using matrix multiplication.

For us to pull out a matrix that describes the movies in our dataframe in terms of content, we might just use the indicator variables related to **year** and **genre** for our movies.  

Then we can obtain a matrix of how similar movies are to one another by taking the dot product of this matrix with itself.  

We can perform the dot product on a matrix of movies with content characteristics to provide a movie by movie matrix where each cell is an indication of how similar two movies are to one another.  




`3.` Create a numpy array that is a matrix of indicator variables related to year (by century) and movie genres by movie.  Perform the dot product of this matrix with itself (transposed) to obtain a similarity matrix of each movie with every other movie.  The final matrix should be 31245 x 31245.

In [15]:
# Subset so movie_content is only using the dummy variables for each genre and the 3 century based year dummy columns
cols = [c for c in movies.columns if c not in {'movie', 'genre', 'date'}]
M = movies[cols].values.astype(np.int8)
print('movies.shape =', movies.shape)
print('M.shape =', M.shape)

# Take the dot product to obtain a movie x movie matrix of similarities
similarity_matrix = (M @ M.T).astype(np.int8)
print('similarity_matrix.shape =', similarity_matrix.shape)

movies.shape = (31245, 34)
M.shape = (31245, 31)
similarity_matrix.shape = (31245, 31245)


In [2]:
# 31245**2 / 2

488125012.5

In [14]:
similarity_matrix[0:10]

array([[3., 3., 3., ..., 0., 0., 0.],
       [3., 3., 3., ..., 0., 0., 0.],
       [3., 3., 3., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [1., 1., 1., ..., 0., 0., 0.],
       [1., 1., 1., ..., 0., 0., 1.]], dtype=float16)

In [16]:
movies.head()

movie  \
movie_id                                                      
8             Edison Kinetoscopic Record of a Sneeze (1894)   
10                      La sortie des usines Lumière (1895)   
12                            The Arrival of a Train (1896)   
25        The Oxford and Cambridge University Boat Race ...   
91                               Le manoir du diable (1896)   

                      genre  date  1800's  1900's  2000's  History  News  \
movie_id                                                                   
8         Documentary|Short  1894       1       0       0        0     0   
10        Documentary|Short  1895       1       0       0        0     0   
12        Documentary|Short  1896       1       0       0        0     0   
25                      NaN  1895       1       0       0        0     0   
91             Short|Horror  1896       1       0       0        0     0   

          Horror  Musical  ...  Fantasy  Romance  Game-Show  Action  \
movie_id                   ...                                        
8              0        0  ...        0        0          0       0   
10             0        0  ...        0        0          0       0   
12             0        0  ...        0        0          0       0   
25             0        0  ...        0        0          0       0   
91             1        0  ...        0        0          0       0   

          Documentary  Animation  Comedy  Short  Western  Thriller  
movie_id                                                            
8                   1          0       0      1        0         0  
10                  1          0       0      1        0         0  
12                  1          0       0      1        0         0  
25                  0          0       0      0        0         0  
91                  0          0       0      1        0         0  

[5 rows x 34 columns]

In [18]:
# create checks for the dot product matrix
assert similarity_matrix.shape[0] == 31245
assert similarity_matrix.shape[1] == 31245
assert similarity_matrix[0, 0] == np.max(similarity_matrix[0])
print("Looks like you passed all of the tests.  Though they weren't very robust - if you want to write some of your own, I won't complain!")

Looks like you passed all of the tests.  Though they weren't very robust - if you want to write some of your own, I won't complain!


### For Each User...


Now you have a matrix where each user has their ratings ordered.  You also have a second matrix where movies are each axis, and the matrix entries are larger where the two movies are more similar and smaller where the two movies are dissimilar.  This matrix is a measure of content similarity. Therefore, it is time to get to the fun part.

For each user, we will perform the following:

    i. For each movie, find the movies that are most similar that the user hasn't seen.

    ii. Continue through the available, rated movies until 10 recommendations or until there are no additional movies.

As a final note, you may need to adjust the criteria for 'most similar' to obtain 10 recommendations.  As a first pass, I used only movies with the highest possible similarity to one another as similar enough to add as a recommendation.

`3.` In the cell below, complete each of the functions needed for making content based recommendations.

In [19]:
movies.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 31245 entries, 8 to 8439854
Data columns (total 34 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   movie        31245 non-null  object
 1   genre        31022 non-null  object
 2   date         31245 non-null  int64 
 3   1800's       31245 non-null  int64 
 4   1900's       31245 non-null  int64 
 5   2000's       31245 non-null  int64 
 6   History      31245 non-null  int64 
 7   News         31245 non-null  int64 
 8   Horror       31245 non-null  int64 
 9   Musical      31245 non-null  int64 
 10  Film-Noir    31245 non-null  int64 
 11  Mystery      31245 non-null  int64 
 12  Adventure    31245 non-null  int64 
 13  Sport        31245 non-null  int64 
 14  War          31245 non-null  int64 
 15  Music        31245 non-null  int64 
 16  Reality-TV   31245 non-null  int64 
 17  Adult        31245 non-null  int64 
 18  Crime        31245 non-null  int64 
 19  Family       31245 non-

In [100]:
movies_index = movies.index.to_numpy()
def get_i_index(movie_id):
    return np.where(movies_index == movie_id)[0][0]
    

def get_movie_names(movie_ids):
    '''
    INPUT
    movie_ids - a list of movie_ids
    OUTPUT
    movies - a list of movie names associated with the movie_ids
    
    '''
    # return a list with movie names for the list of input movie IDs
    movie_list = movies.iloc[movie_ids, 0].tolist()   
    return movie_list



def find_similar_movies(movie_id, n=None):
    '''
    INPUT
    movie_id - a movie_id 
    OUTPUT
    similar_movies - an array of the most similar movies by title
    '''
    # find the row of each movie id
    i_idx = get_i_index(movie_id)
    print('i_idx =', i_idx)
    movie_row = similarity_matrix[i_idx]
    print('movie_row =', movie_row)
    
    # find the most similar movie indices - to start I said they need to be the same for all content
    max_sim_idx = np.flip(np.argsort(movie_row))
    if n:
        max_sim_idx = max_sim_idx[1:n+1]
    else:
        max_sim_idx = max_sim_idx[1:]
    
    print('max_sim_idx =', max_sim_idx)
    # pull the movie titles based on the indices
    similar_movies = get_movie_names(max_sim_idx)
    
    return similar_movies
    



def make_recs(n_top=10):
    '''
    INPUT
    None
    OUTPUT
    recs - a dictionary with keys of the user and values of the recommendations
    '''
    # Create dictionary to return with users and ratings
    recs = {}
    i = 0    
    # For each user
    for uid in users_who_need_recs:
        # watch progress
        i += 1
        print('progress =', i*100/len(users_who_need_recs), '%')
        
        # Pull only the reviews the user has seen and liked.
        user_reviews = ranked_ratings[(ranked_ratings['user_id'] == uid) & (ranked_ratings['rating'] > 6)]
        # Look at each of the movies (highest ranked first),
        if len(user_reviews) > 0:
            user_movies = user_reviews[['movie_id', 'rating']].set_index('movie_id')
            # get indices for i_loc
            movies_idx = [get_i_index(movie_id) for movie_id in user_movies.index]
            # Extract those rows from similarity matrix
            movies_sims = similarity_matrix[movies_idx]
            # Run weighted avg on rating and similarity 
            ratings = user_movies['rating'].to_numpy().reshape(-1, 1)
            most_sim_movies = np.sum(movies_sims * ratings, axis=0) / np.sum(ratings)
            # sort descending
            most_sim_movies = np.flip(np.argsort(most_sim_movies))
            # assert the movies is new to the user
            s = set(movies_idx)
            res = [mid for mid in most_sim_movies if mid not in s]
            # get n_top movies
            recs[uid] = [get_movie_names(res[:n_top])]
        # pull the movies the user hasn't seen that are most similar
        # These will be the recommendations - continue until 10 recs 
        # or you have depleted the movie list for the user
    return recs

In [101]:
result = make_recs()

len(result)

progress = 0.0031465340926968943 %
progress = 0.006293068185393789 %
progress = 0.009439602278090682 %
progress = 0.012586136370787577 %
progress = 0.01573267046348447 %
progress = 0.018879204556181365 %
progress = 0.02202573864887826 %
progress = 0.025172272741575154 %
progress = 0.02831880683427205 %
progress = 0.03146534092696894 %
progress = 0.03461187501966584 %
progress = 0.03775840911236273 %
progress = 0.04090494320505963 %
progress = 0.04405147729775652 %
progress = 0.04719801139045342 %
progress = 0.05034454548315031 %
progress = 0.05349107957584721 %
progress = 0.0566376136685441 %
progress = 0.05978414776124099 %
progress = 0.06293068185393788 %
progress = 0.06607721594663478 %
progress = 0.06922375003933168 %
progress = 0.07237028413202858 %
progress = 0.07551681822472546 %
progress = 0.07866335231742236 %
progress = 0.08180988641011926 %
progress = 0.08495642050281615 %
progress = 0.08810295459551304 %
progress = 0.09124948868820994 %
progress = 0.09439602278090684 %
prog

progress = 0.8180988641011926 %
progress = 0.8212453981938894 %
progress = 0.8243919322865864 %
progress = 0.8275384663792832 %
progress = 0.8306850004719801 %
progress = 0.833831534564677 %
progress = 0.8369780686573739 %
progress = 0.8401246027500708 %
progress = 0.8432711368427677 %
progress = 0.8464176709354646 %
progress = 0.8495642050281614 %
progress = 0.8527107391208584 %
progress = 0.8558572732135553 %
progress = 0.8590038073062521 %
progress = 0.8621503413989491 %
progress = 0.8652968754916459 %
progress = 0.8684434095843429 %
progress = 0.8715899436770398 %
progress = 0.8747364777697366 %
progress = 0.8778830118624336 %
progress = 0.8810295459551304 %
progress = 0.8841760800478273 %
progress = 0.8873226141405242 %
progress = 0.8904691482332211 %
progress = 0.893615682325918 %
progress = 0.8967622164186149 %
progress = 0.8999087505113118 %
progress = 0.9030552846040086 %
progress = 0.9062018186967056 %
progress = 0.9093483527894025 %
progress = 0.9124948868820993 %
progress =

progress = 1.6330511941096881 %
progress = 1.6361977282023852 %
progress = 1.639344262295082 %
progress = 1.6424907963877788 %
progress = 1.6456373304804757 %
progress = 1.6487838645731727 %
progress = 1.6519303986658695 %
progress = 1.6550769327585664 %
progress = 1.6582234668512634 %
progress = 1.6613700009439603 %
progress = 1.664516535036657 %
progress = 1.667663069129354 %
progress = 1.670809603222051 %
progress = 1.6739561373147478 %
progress = 1.6771026714074446 %
progress = 1.6802492055001417 %
progress = 1.6833957395928385 %
progress = 1.6865422736855353 %
progress = 1.6896888077782324 %
progress = 1.6928353418709292 %
progress = 1.695981875963626 %
progress = 1.6991284100563229 %
progress = 1.70227494414902 %
progress = 1.7054214782417167 %
progress = 1.7085680123344136 %
progress = 1.7117145464271106 %
progress = 1.7148610805198075 %
progress = 1.7180076146125043 %
progress = 1.7211541487052011 %
progress = 1.7243006827978982 %
progress = 1.727447216890595 %
progress = 1.730

progress = 2.460589660488971 %
progress = 2.4637361945816685 %
progress = 2.4668827286743653 %
progress = 2.470029262767062 %
progress = 2.473175796859759 %
progress = 2.476322330952456 %
progress = 2.4794688650451526 %
progress = 2.4826153991378495 %
progress = 2.4857619332305467 %
progress = 2.4889084673232436 %
progress = 2.4920550014159404 %
progress = 2.495201535508637 %
progress = 2.498348069601334 %
progress = 2.501494603694031 %
progress = 2.5046411377867277 %
progress = 2.507787671879425 %
progress = 2.510934205972122 %
progress = 2.5140807400648186 %
progress = 2.5172272741575155 %
progress = 2.5203738082502123 %
progress = 2.523520342342909 %
progress = 2.5266668764356064 %
progress = 2.529813410528303 %
progress = 2.532959944621 %
progress = 2.536106478713697 %
progress = 2.5392530128063937 %
progress = 2.5423995468990905 %
progress = 2.5455460809917874 %
progress = 2.5486926150844846 %
progress = 2.5518391491771815 %
progress = 2.5549856832698783 %
progress = 2.55813221736

progress = 3.3007142632390423 %
progress = 3.303860797331739 %
progress = 3.307007331424436 %
progress = 3.3101538655171328 %
progress = 3.3133003996098296 %
progress = 3.316446933702527 %
progress = 3.3195934677952237 %
progress = 3.3227400018879205 %
progress = 3.3258865359806173 %
progress = 3.329033070073314 %
progress = 3.332179604166011 %
progress = 3.335326138258708 %
progress = 3.338472672351405 %
progress = 3.341619206444102 %
progress = 3.3447657405367988 %
progress = 3.3479122746294956 %
progress = 3.3510588087221924 %
progress = 3.3542053428148892 %
progress = 3.357351876907586 %
progress = 3.3604984110002833 %
progress = 3.36364494509298 %
progress = 3.366791479185677 %
progress = 3.369938013278374 %
progress = 3.3730845473710707 %
progress = 3.3762310814637675 %
progress = 3.3793776155564648 %
progress = 3.3825241496491616 %
progress = 3.3856706837418584 %
progress = 3.3888172178345553 %
progress = 3.391963751927252 %
progress = 3.395110286019949 %
progress = 3.3982568201

...

progress = 96.90695698687895 %
progress = 96.91010352097165 %
progress = 96.91325005506435 %
progress = 96.91639658915705 %
progress = 96.91954312324974 %
progress = 96.92268965734243 %
progress = 96.92583619143514 %
progress = 96.92898272552783 %
progress = 96.93212925962052 %
progress = 96.93527579371323 %
progress = 96.93842232780592 %
progress = 96.94156886189862 %
progress = 96.94471539599131 %
progress = 96.94786193008402 %
progress = 96.95100846417671 %
progress = 96.9541549982694 %
progress = 96.95730153236211 %
progress = 96.9604480664548 %
progress = 96.9635946005475 %
progress = 96.96674113464019 %
progress = 96.9698876687329 %
progress = 96.97303420282559 %
progress = 96.97618073691828 %
progress = 96.97932727101099 %
progress = 96.98247380510368 %
progress = 96.98562033919637 %
progress = 96.98876687328907 %
progress = 96.99191340738177 %
progress = 96.99505994147447 %
progress = 96.99820647556716 %
progress = 97.00135300965987 %
progress = 97.00449954375256 %
progress = 9

progress = 97.7691073282779 %
progress = 97.7722538623706 %
progress = 97.7754003964633 %
progress = 97.77854693055599 %
progress = 97.78169346464868 %
progress = 97.78483999874139 %
progress = 97.78798653283408 %
progress = 97.79113306692678 %
progress = 97.79427960101948 %
progress = 97.79742613511218 %
progress = 97.80057266920487 %
progress = 97.80371920329756 %
progress = 97.80686573739027 %
progress = 97.81001227148296 %
progress = 97.81315880557565 %
progress = 97.81630533966836 %
progress = 97.81945187376105 %
progress = 97.82259840785375 %
progress = 97.82574494194644 %
progress = 97.82889147603915 %
progress = 97.83203801013184 %
progress = 97.83518454422453 %
progress = 97.83833107831724 %
progress = 97.84147761240993 %
progress = 97.84462414650262 %
progress = 97.84777068059532 %
progress = 97.85091721468802 %
progress = 97.85406374878072 %
progress = 97.85721028287341 %
progress = 97.86035681696612 %
progress = 97.86350335105881 %
progress = 97.8666498851515 %
progress = 9

progress = 98.61867153330607 %
progress = 98.62181806739876 %
progress = 98.62496460149146 %
progress = 98.62811113558415 %
progress = 98.63125766967686 %
progress = 98.63440420376955 %
progress = 98.63755073786224 %
progress = 98.64069727195495 %
progress = 98.64384380604764 %
progress = 98.64699034014033 %
progress = 98.65013687423303 %
progress = 98.65328340832573 %
progress = 98.65642994241843 %
progress = 98.65957647651112 %
progress = 98.66272301060383 %
progress = 98.66586954469652 %
progress = 98.66901607878921 %
progress = 98.6721626128819 %
progress = 98.67530914697461 %
progress = 98.6784556810673 %
progress = 98.68160221516 %
progress = 98.6847487492527 %
progress = 98.6878952833454 %
progress = 98.69104181743809 %
progress = 98.69418835153078 %
progress = 98.69733488562349 %
progress = 98.70048141971618 %
progress = 98.70362795380888 %
progress = 98.70677448790158 %
progress = 98.70992102199428 %
progress = 98.71306755608697 %
progress = 98.71621409017966 %
progress = 98.7

progress = 99.48396840879771 %
progress = 99.4871149428904 %
progress = 99.49026147698311 %
progress = 99.4934080110758 %
progress = 99.4965545451685 %
progress = 99.4997010792612 %
progress = 99.5028476133539 %
progress = 99.50599414744659 %
progress = 99.50914068153928 %
progress = 99.51228721563199 %
progress = 99.51543374972468 %
progress = 99.51858028381737 %
progress = 99.52172681791008 %
progress = 99.52487335200277 %
progress = 99.52801988609546 %
progress = 99.53116642018816 %
progress = 99.53431295428086 %
progress = 99.53745948837356 %
progress = 99.54060602246625 %
progress = 99.54375255655896 %
progress = 99.54689909065165 %
progress = 99.55004562474434 %
progress = 99.55319215883704 %
progress = 99.55633869292974 %
progress = 99.55948522702244 %
progress = 99.56263176111513 %
progress = 99.56577829520783 %
progress = 99.56892482930053 %
progress = 99.57207136339322 %
progress = 99.57521789748591 %
progress = 99.57836443157862 %
progress = 99.58151096567131 %
progress = 99

27829

In [91]:
get_movie_names([2]) # 8, 10, 12

['The Arrival of a Train (1896)']

In [92]:
find_similar_movies(91)

i_idx = 4
movie_row = [2 2 2 ... 0 0 0]
max_sim_idx = [    4     0 24138 ... 19900 19901 15622]


['Le manoir du diable (1896)',
 'Edison Kinetoscopic Record of a Sneeze (1894)',
 'Broken Night (2013)',
 "Director's Cut (2015)",
 'Banana Motherfucker (2011)',
 'Isolated (2015)',
 'Treevenge (2008)',
 'Maniac 2: Mr. Robbie (1986)',
 'The Tour (2014)',
 'Jack Attack (2013)',
 'Roadkill: The Last Days of John Martin (1994)',
 'He Took His Skin Off for Me (2014)',
 'Zombie Playground: Ice Scream (2016)',
 'Mamá (2008)',
 'Crack Dog (1988)',
 'The Soldier (2007)',
 'Bread Crumbs (2009)',
 'Night of the Sea Monkey: A Disturbing Tale (2013)',
 'Attic Entity (2014)',
 'Mr. Dentonn (2014)',
 'Saw (2003)',
 'Yours Truly (2011)',
 'Angels (2013)',
 'Todd Sloane (2016)',
 'Shell Shocked (2013)',
 'Zygote (2017)',
 'La leyenda del espantapájaros (2005)',
 'The Kiss (1896)',
 'Aftermath (1994)',
 'Zánik domu Usheru (1982)',
 'The Grandmother (1970)',
 'Ghosts (1997)',
 "My Enemy's Son (2012)",
 'Muralim (2011)',
 'Self-Assembly (2014)',
 'Sallie Gardner at a Gallop (1878)',
 'Lights Out (2013)',

In [ ]:
recs = make_recs()

### How Did We Do?

Now that you have made the recommendations, how did we do in providing everyone with a set of recommendations?

`4.` Use the cells below to see how many individuals you were able to make recommendations for, as well as explore characteristics about individuals for whom you were not able to make recommendations.  

In [102]:
# Some characteristics of my content based recommendations
users_without_all_recs = [k for k in result if len(result[k]) < 10] #store user ids without recs
users_with_all_recs = [k for k in users_with_all_recs] + [k for k in result] # users with all recs here
no_recs = [uid for uid in users_who_need_recs if result.get(uid) is None]# users with no recommendations

print("There were {} users without all 10 recommendations we would have liked to have.".format(len(users_without_all_recs)))
print("There were {} users with all 10 recommendations we would like them to have.".format(len(users_with_all_recs)))
print("There were {} users with no recommendations at all!".format(len(no_recs)))

There were 27829 users without all 10 recommendations we would have liked to have.
There were 50016 users with all 10 recommendations we would like them to have.
There were 3952 users with no recommendations at all!
